# <p style="padding: 15px; background-color: #010D36; font-family: 'JetBrains Mono'; font-weight: bold; font-size: 100%; color: #F2F2F0; letter-spacing: 2px; text-align: center; border-radius: 8px;">ICR - Identifying Age-Related Conditions</p>

In [245]:
import os
import shutil
import subprocess
from collections import defaultdict
from copy import copy
from itertools import product
from functools import reduce
from pathlib import Path

# Sub-modules and so on.
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.figure_factory as ff
import plotly.graph_objects as go
import seaborn as sns
import scipy.stats as stats
from colorama import Fore, Style
from IPython.core.display import HTML
from IPython.display import display_html
from matplotlib.colors import Colormap
from plotly.subplots import make_subplots
from scipy.cluster.hierarchy import fcluster, linkage
from scipy.spatial.distance import squareform
from scipy.stats import gaussian_kde, probplot
from sklearn.preprocessing import PowerTransformer

ON_KAGGLE = os.getenv("KAGGLE_KERNEL_RUN_TYPE") is not None

# Colorama settings.
CLR = (Style.BRIGHT + Fore.BLACK) if ON_KAGGLE else (Style.BRIGHT + Fore.WHITE)
RED = Style.BRIGHT + Fore.RED
BLUE = Style.BRIGHT + Fore.BLUE
CYAN = Style.BRIGHT + Fore.CYAN
RESET = Style.RESET_ALL

# Colors
DF_CMAP: Colormap = sns.light_palette("#8C92AC", as_cmap=True)  # type: ignore
FONT_COLOR = "#010D36"
BACKGROUND_COLOR = "#F6F5F5"

cell_hover = {  # for row hover use <tr> instead of <td>
    "selector": "td:hover",
    "props": "background-color: #F6F5F5",
}
text_highlight = {
    "selector": "td",
    "props": "color: #FF2079; font-weight: bold",
}
index_names = {
    "selector": ".index_name",
    "props": "font-style: italic; background-color: #010D36; color: #F2F2F0;",
}
headers = {
    "selector": "th:not(.index_name)",
    "props": "font-style: italic; background-color: #010D36; color: #F2F2F0;",
}
DF_STYLE = (cell_hover, index_names, headers, text_highlight)

MY_RC = {
    "axes.labelcolor": FONT_COLOR,
    "axes.labelsize": 10,
    "axes.labelpad": 15,
    "axes.labelweight": "bold",
    "axes.titlesize": 14,
    "axes.titleweight": "bold",
    "axes.titlepad": 15,
    "axes.facecolor": BACKGROUND_COLOR,
    "xtick.labelsize": 10,
    "xtick.color": FONT_COLOR,
    "ytick.labelsize": 10,
    "ytick.color": FONT_COLOR,
    "figure.titlesize": 14,
    "figure.titleweight": "bold",
    "figure.facecolor": BACKGROUND_COLOR,
    "figure.edgecolor": BACKGROUND_COLOR,
    "figure.dpi": 72,  # Locally Seaborn uses 72, meanwhile Kaggle 96.
    "font.size": 10,
    "font.family": "Serif",
    "text.color": FONT_COLOR,
}
sns.set_theme(rc=MY_RC)


# Utility functions.
def download_dataset_from_kaggle(user, dataset, directory):
    command = "kaggle datasets download -d "
    filepath = directory / (dataset + ".zip")

    if not filepath.is_file():
        subprocess.run((command + user + "/" + dataset).split())
        filepath.parent.mkdir(parents=True, exist_ok=True)
        shutil.unpack_archive(dataset + ".zip", "data")
        shutil.move(dataset + ".zip", "data")


def download_competition_from_kaggle(competition):
    command = "kaggle competitions download -c "
    filepath = Path("data/" + competition + ".zip")

    if not filepath.is_file():
        subprocess.run((command + competition).split())
        Path("data").mkdir(parents=True, exist_ok=True)
        shutil.unpack_archive(competition + ".zip", "data")
        shutil.move(competition + ".zip", "data")


# Html `code` block highlight.
HTML(
    """
<style>
code {
    background: rgba(58, 90, 129, 0.5) !important;
    border-radius: 4px !important;
    color: #f2f2f0 !important;
}
</style>
"""
)


<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
">
    <b>Competition Description</b> 📜
</p>

<p style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 20px;
    margin-right: 20px;
    margin-bottom: 20px;
">
    <i>The goal of this competition is to predict if a person has any of three medical conditions. You are being asked to predict if the person has one or more of any of the three medical conditions (Class $1$), or none of the three medical conditions (Class $0$). You will create a model trained on measurements of health characteristics.</br></br>
    To determine if someone has these medical conditions requires a long and intrusive process to collect information from patients. With predictive models, we can shorten this process and keep patient details private by collecting key characteristics relative to the conditions, then encoding these characteristics.</br></br>
    Your work will help researchers discover the relationship between measurements of certain characteristics and potential patient conditions.</i>
</p>

<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color:#f2f2f0;
">
    <b>Context and Task</b> 🕵
</p>

<p style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 20px;
    margin-right: 20px;
    margin-bottom: 20px;
">
    <i>They say age is just a number but a whole host of health issues come with aging. From heart disease and dementia to hearing loss and arthritis, aging is a risk factor for numerous diseases and complications. The growing field of bioinformatics includes research into interventions that can help slow and reverse biological aging and prevent major age-related ailments. Data science could have a role to play in developing new methods to solve problems with diverse data, even if the number of samples is small.</br></br>
    Currently, models like XGBoost and random forest are used to predict medical conditions yet the models' performance is not good enough. Dealing with critical problems where lives are on the line, models need to make correct predictions reliably and consistently between different cases.</br></br>
    Founded in 2015, competition host InVitro Cell Research, LLC (ICR) is a privately funded company focused on regenerative and preventive personalized medicine. Their offices and labs in the greater New York City area offer state-of-the-art research space. InVitro Cell Research's Scientists are what set them apart, helping guide and defining their mission of researching how to repair aging people fast.</br></br>
    <b>In this competition, you’ll work with measurements of health characteristic data to solve critical problems in bioinformatics. Based on minimal training, you’ll create a model to predict if a person has any of three medical conditions, with an aim to improve on existing methods.</b></br></br>
    You could help advance the growing field of bioinformatics and explore new methods to solve complex problems with diverse data.</i>
</p>

<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
">
    <b>This Notebook Covers</b> 📔
</p>

<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-bottom: 20px;
"> 
    <li>A quick look at the dataset.</li>
    <li>...</li>
</ul>

<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
">
    <b>See More Here</b> 📈
</p>

<p style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 20px;
    margin-right: 20px;
    margin-bottom: 20px;
">
    <a href="https://www.kaggle.com/competitions/icr-identify-age-related-conditions/overview" style="color: #01CBEE;"><b>ICR - Identifying Age-Related Conditions</b></a>
</p>
</blockquote>

# <p style="padding: 15px; background-color: #010D36; font-family: 'JetBrains Mono'; font-weight: bold; font-size: 100%; color: #f2f2f0; letter-spacing: 2px; text-align: center; border-radius: 8px;">Quick Overview</p>

<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Notes</b> 📜
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>Let's get started with a short dataset overview.</li>
</ul>
</blockquote>

In [2]:
competition = "icr-identify-age-related-conditions"

if not ON_KAGGLE:
    download_competition_from_kaggle(competition)
    train_path = "data/train.csv"
    test_path = "data/test.csv"
    greeks_path = "data/greeks.csv"
else:
    train_path = f"/kaggle/input/{competition}/train.csv"
    test_path = f"/kaggle/input/{competition}/test.csv"
    greeks_path = f"/kaggle/input/{competition}/greeks.csv"

train = pd.read_csv(train_path, index_col="Id").rename(columns=str.strip)
test = pd.read_csv(test_path, index_col="Id").rename(columns=str.strip)
greeks = pd.read_csv(greeks_path, index_col="Id").rename(columns=str.strip)


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>General Remarks</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">

<p style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 20px;
    margin-right: 20px;
    margin-bottom: 20px;
">
    <b>In the original description, we read that:</b></br></br>
    <i>The competition data comprises over fifty anonymized health characteristics linked to three age-related conditions. Your goal is to predict whether a subject has or has not been diagnosed with one of these conditions - a binary classification problem.</br></br>
    Note that this is a Code Competition, in which the actual test set is hidden. In this version, we give some sample data in the correct format to help you author your solutions. When your submission is scored, this example test data will be replaced with the full test set. There are about $400$ rows in the full test set.</i>
</p>

<p style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 20px;
    margin-right: 20px;
    margin-bottom: 20px;
">
    <b>Moreover, we know that:</b>
</p>

<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li><b>train.csv</b> - <i>The training set.</i></li>
    <ul style="
        font-size: 16px;
        font-family: 'JetBrains Mono';
        color: #f2f2f0;
        margin-right: 8px;
    ">
        <li><code>Id</code> - <i>Unique identifier for each observation.</i></li>
        <li><code>AB-GL</code> - <i>Fifty-six anonymized health characteristics. All are numeric except for EJ, which is categorical.</i></li>
        <li><code>Class</code> - <i>A binary target: $1$ indicates the subject has been diagnosed with one of the three conditions, $0$ indicates they have not.</i></li>
    </ul>
    <li><b>test.csv</b> - <i>The test set. Your goal is to predict the probability that a subject in this set belongs to each of the two classes.</i></li>
    <li><b>greeks.csv</b> - <i>Supplemental metadata, only available for the training set.</i></li>
    <ul style="
        font-size: 16px;
        font-family: 'JetBrains Mono';
        color: #f2f2f0;
        margin-right: 8px;
    ">
        <li><code>Alpha</code> - <i>Identifies the type of age-related condition, if present.</i></li>
        <ul style="
            font-size: 16px;
            font-family: 'JetBrains Mono';
            color: #f2f2f0;
            margin-right: 8px;
        ">
            <li><code>A</code> - <i>No age-related condition. Corresponds to class $0$.</i></li>
            <li><code>B</code>, <code>D</code>, <code>G</code> - <i>The three age-related conditions. Correspond to class $1$.</i></li>
        </ul>
        <li><code>Beta</code>, <code>Gamma</code>, <code>Delta</code> - <i>Three experimental characteristics.</i></li>
        <li><code>Epsilon</code> - <i>The date the data for this subject was collected. Note that all of the data in the test set was collected after the training set was collected.</i></li>
    </ul>
</ul>
</blockquote>

In [3]:
train.head().style.set_table_styles(DF_STYLE).format(precision=3)


In [4]:
train.info(verbose=False)


<class 'pandas.core.frame.DataFrame'>
Index: 617 entries, 000ff2bfdfe9 to ffcca4ded3bb
Columns: 57 entries, AB to Class
dtypes: float64(55), int64(1), object(1)
memory usage: 279.6+ KB


In [5]:
greeks.head().style.set_table_styles(DF_STYLE)


In [6]:
greeks.info(verbose=False)


<class 'pandas.core.frame.DataFrame'>
Index: 617 entries, 000ff2bfdfe9 to ffcca4ded3bb
Columns: 5 entries, Alpha to Epsilon
dtypes: object(5)
memory usage: 28.9+ KB


In [7]:
missing_values_cols = train.isna().sum()[train.isna().sum() > 0].index.to_list()

print(CLR + "Training Dataset Missing Values\n")

for feature in missing_values_cols:
    print(
        (CLR + feature) + "\t",
        (RED + str(train[feature].isna().sum())) + "\t",
        (RED + f"{train[feature].isna().sum() / len(train):.1%}" + RESET) + "\t",
        (RED + f"{train[feature].dtype}"),
    )


Training Dataset Missing Values

BQ	 60	 9.7%	 float64
CB	 2	 0.3%	 float64
CC	 3	 0.5%	 float64
DU	 1	 0.2%	 float64
EL	 60	 9.7%	 float64
FC	 1	 0.2%	 float64
FL	 1	 0.2%	 float64
FS	 2	 0.3%	 float64
GL	 1	 0.2%	 float64


In [8]:
fig = px.pie(
    train.assign(ClassMap=train.Class.map({0: "Class 0", 1: "Class 1"})),
    names="ClassMap",
    height=540,
    width=840,
    hole=0.65,
    title="Target Overview - Class",
    color_discrete_sequence=["#010D36", "#FF2079"],
)
fig.update_layout(
    font_color=FONT_COLOR,
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    showlegend=False,
)
fig.add_annotation(
    x=0.5,
    y=0.5,
    align="center",
    xref="paper",
    yref="paper",
    showarrow=False,
    font_size=22,
    text="Class<br>Unbalance",
)
fig.update_traces(
    hovertemplate=None,
    textposition="outside",
    texttemplate="%{label}<br>%{value} - %{percent}",
    textfont_size=16,
    rotation=-20,
    marker_line_width=25,
    marker_line_color=BACKGROUND_COLOR,
)
fig.show()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>The training dataset is small, containing $617$ samples. Nevertheless, we have to handle $57$ different medical characteristics (attributes), including the binary target.</li>
    <li>These features are anonymous, and we all know that these are specific medical characteristics.</li>
    <li>We've got additional data, e.g. greeks.csv, but we will look at this later, especially the <code>Epsilon</code> attribute.</li>
    <li>In our dataset, we have nine numeric features that contain missing values. Typically, only $1$ to $3$ values are missing for each attribute. However, there are two specific features where we observe $60$ missing values each.</li>
    <li>Lastly, there is quite a lot of unbalance in the target: 83% to 17%.</li>
</ul>
</blockquote>

# <p style="padding: 15px; background-color: #010D36; font-family: 'JetBrains Mono'; font-weight: bold; font-size: 100%; color: #f2f2f0; letter-spacing: 2px; text-align: center; border-radius: 8px;">Basic Relations in Numerical Features</p>

<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Notes</b> 📜
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>Let's focus on an elementary description of numerical features. Firstly, let's see the numerical summary. Then, we will get to the correlation matrix and finally create hierarchical clustering based on Pearson correlations.</li>
</ul>
</blockquote>

In [9]:
numeric_descr = (
    train.drop("Class", axis=1)
    .describe(percentiles=[0.01, 0.05, 0.25, 0.50, 0.75, 0.95, 0.99])
    .drop("count")
    .T.rename(columns=str.title)
)

numeric_descr.style.set_table_styles(DF_STYLE).format(precision=3)


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>Well, at first glance, it's hard to focus on specific values here. However, let's look at the Q1-Q3 range and upper percentiles, including the max value. We may conclude that many of these distributions have long tails, which will probably require some transformations like log-level transformation.</li>
</ul>
</blockquote>

In [10]:
color_map = [[0.0, "#01CBEE"], [0.5, "#010D36"], [1.0, "#FF2079"]]

pearson_corr = (
    train.drop("Class", axis=1).corr(numeric_only=True, method="pearson").round(2)
)
mask = np.triu(np.ones_like(pearson_corr, dtype=bool))
lower_triangular_corr = (
    pearson_corr.mask(mask)
    .dropna(axis="index", how="all")
    .dropna(axis="columns", how="all")
)

heatmap = go.Heatmap(
    z=lower_triangular_corr,
    x=lower_triangular_corr.columns,
    y=lower_triangular_corr.index,
    text=lower_triangular_corr.fillna(""),
    texttemplate="%{text}",
    xgap=1,
    ygap=1,
    showscale=True,
    colorscale=color_map,
    colorbar_len=1.02,
    hoverinfo="none",
)
fig = go.Figure(heatmap)
fig.update_layout(
    font_color=FONT_COLOR,
    title="Correlation Matrix (Pearson) - Lower Triangular",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    width=840,
    height=840,
    xaxis_showgrid=False,
    yaxis_showgrid=False,
    yaxis_autorange="reversed",
)
fig.show()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>Here we have several highly correlated features like <code>BZ</code> vs <code>BC</code> ($0.91$) or <code>DV</code> vs <code>CL</code> ($0.95$). Such extreme linear correlation gives hope for rejecting certain features. Remember that you can zoom in on this matrix and explore specific relations. In the other case, you won't be able to see anything.</li>
</ul>
</blockquote>

In [126]:
dissimilarity = 1 - np.abs(pearson_corr)

fig = ff.create_dendrogram(
    dissimilarity,
    labels=pearson_corr.columns,
    orientation="left",
    colorscale=px.colors.sequential.YlGnBu_r,
    # squareform() returns lower triangular in compressed form - as 1D array.
    linkagefun=lambda x: linkage(squareform(dissimilarity), method="complete"),
)
fig.update_layout(
    font_color=FONT_COLOR,
    title="Hierarchical Clustering using Correlation Matrix (Pearson)",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    height=1340,
    width=840,
    yaxis=dict(
        showline=False,
        title="Feature",
        ticks="",
    ),
    xaxis=dict(
        showline=False,
        title="Distance",
        ticks="",
        range=[-0.05, 1.05],
    ),
)
fig.update_traces(line_width=1.5)
fig.show()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>Okay, here we need to make something clear. Since we had the correlation matrix, we conducted hierarchical clustering. This process consists of an alternative to the K-Means algorithm. Hierarchical clustering allows us to visualize the effect of different clusters' number determining.</li>
    <li>However, relying on a correlation matrix to perform hierarchical clustering requires additional steps. Primarily, clustering methods measure the dissimilarity of variables. Meanwhile, correlation measures similarity. We can treat dissimilarity as $dissimilarity = 1 - abs(correlation)$. And basically, that's all. We passed dissimilarity to the <code>linkage()</code> function from the <code>scipy</code> module and got clustering results.</li>
    <li>Moreover, we should remember that we rely on the <b>Pearson</b> correlation. It measures linear dependency, and it's computed on actual values. However, we could have used for example the <b>Spearman</b> correlation, which is based on ranks and measures monotonic relations.</li>
    <li>Additionally, we chose the <code>complete</code> method in the <code>linkage()</code> function, and if you take a different method, you get different results.</li>
    <li>As you can see, here we have minimal distances between <code>BZ</code> - <code>BC</code>, <code>DV</code> - <code>CL</code>, and <code>EH</code> - <code>FD</code>.</li>
</ul>
</blockquote>

# <p style="padding: 15px; background-color: #010D36; font-family: 'JetBrains Mono'; font-weight: bold; font-size: 100%; color: #f2f2f0; letter-spacing: 2px; text-align: center; border-radius: 8px;">Kernel Density Estimation &amp; Pair Plots</p>

<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Notes</b> 📜
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>In this section, we will focus on exploring distributions in a general manner. Firstly, we will depict some pair plots of highly correlated features, and then we will see the probability density of these variables by target value.</li>
    <li>Firstly, let's define some small utility functions. The former is liable for KDE calculations, and the latter provides appropriate axes arrangement.</li>
</ul>
</blockquote>

In [138]:
def get_kde_estimation(data_series):
    kde = gaussian_kde(data_series.dropna())
    kde_range = np.linspace(
        data_series.min() - data_series.max() * 0.1,
        data_series.max() + data_series.max() * 0.1,
        len(data_series),
    )
    estimated_values = kde.evaluate(kde_range)
    estimated_values_cum = np.cumsum(estimated_values)
    estimated_values_cum /= estimated_values_cum.max()
    return kde_range, estimated_values, estimated_values_cum


def get_n_rows_axes(n_features, n_cols=5, n_rows=None):
    n_rows = int(np.ceil(n_features / n_cols))
    current_col = range(1, n_cols + 1)
    current_row = range(1, n_rows + 1)
    return n_rows, list(product(current_row, current_col))


In [139]:
threshold = 0.7

highest_abs_corr = (
    lower_triangular_corr.abs()
    .unstack()
    .sort_values(ascending=False)  # type: ignore
    .rename("Absolute Pearson Correlation")
)

highest_abs_corr = (
    highest_abs_corr[highest_abs_corr > threshold]
    .to_frame()
    .reset_index(names=["Feature 1", "Feature 2"])
)

highest_corr_combinations = highest_abs_corr[["Feature 1", "Feature 2"]].to_numpy()
highest_abs_corr.style.set_table_styles(DF_STYLE).format(precision=2)


In [140]:
n_cols = 3
n_rows, axes = get_n_rows_axes(len(highest_corr_combinations), n_cols=n_cols)

fig = make_subplots(
    rows=n_rows,
    cols=n_cols,
    horizontal_spacing=0.1,
    vertical_spacing=0.06,
)

show_legend = True

for k, ((current_row, current_col), (feature1, feature2)) in enumerate(
    zip(axes, highest_corr_combinations)
):
    if k > 0:
        show_legend = False

    fig.add_scatter(
        x=train.query("Class == 0")[feature1],
        y=train.query("Class == 0")[feature2],
        mode="markers",
        name="Class 0",
        marker=dict(color="#010D36", size=3, symbol="diamond", opacity=0.5),
        legendgroup="Class 0",
        showlegend=show_legend,
        row=current_row,
        col=current_col,
    )
    fig.add_scatter(
        x=train.query("Class == 1")[feature1],
        y=train.query("Class == 1")[feature2],
        mode="markers",
        name="Class 1",
        marker=dict(color="#FF2079", size=2, symbol="circle", opacity=0.5),
        legendgroup="Class 1",
        showlegend=show_legend,
        row=current_row,
        col=current_col,
    )
    fig.update_xaxes(
        type="log",
        title_text=feature1,
        titlefont_size=9,
        titlefont_family="Arial Black",
        tickfont_size=7,
        row=current_row,
        col=current_col,
    )
    fig.update_yaxes(
        type="log",
        title_text=feature2,
        titlefont_size=9,
        titlefont_family="Arial Black",
        tickfont_size=7,
        row=current_row,
        col=current_col,
    )

fig.update_annotations(font_size=14)
fig.update_layout(
    font_color=FONT_COLOR,
    title="Highest Pearson Correlations - Pair Plots<br>Double Logarithmic Scale",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    width=840,
    height=1140,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        xanchor="right",
        y=1.01,
        x=1,
        itemsizing="constant",
    ),
)

fig.show()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>In the case of this dataset, it's impossible to show all pair-plots, so I chose only those most correlated.</li>
    <li>The highest correlation is between <code>EH</code> - <code>FD</code> ($0.97$), and this is clearly visible there. Moreover, values associated with Class $0$ are shifted towards higher values. You can explore this by turning off and turning on a given group using legend. A similar situation occurs within <code>DU</code> - <code>EH</code> and <code>DU</code> - <code>FD</code>. Unfortunately, we don't know what these abbreviations mean.</li>
    <li>Moreover, we can see that many different values of a given feature correspond to one specific value from the second one. It may account for a little problem for machine learning algorithms. Such a situation appears in each of the above relationships.</li>
</ul>
</blockquote>

In [141]:
numeric_data = train.select_dtypes("number")
numeric_cols = numeric_data.drop("Class", axis=1).columns.tolist()

n_cols = 5
n_rows, axes = get_n_rows_axes(len(numeric_cols))

fig1 = make_subplots(
    rows=n_rows,
    cols=n_cols,
    y_title="Probability Density",
    horizontal_spacing=0.06,
    vertical_spacing=0.04,
)
fig2 = copy(fig1)

show_legend = True

for k, ((current_row, current_col), feature) in enumerate(zip(axes, numeric_cols)):
    if k > 0:
        show_legend = False

    for target, color in zip((0, 1), ("#010D36", "#FF2079")):
        kde_range, estimated_values, estimated_values_cum = get_kde_estimation(
            numeric_data.query(f"Class == {target}")[feature]
        )

        for fig, kde_values in zip(  # type: ignore
            (fig1, fig2), (estimated_values, estimated_values_cum)
        ):
            fig.add_scatter(
                x=kde_range,
                y=kde_values,
                line=dict(dash="solid", color=color, width=1),
                fill="tozeroy",
                name=f"Class {target}",
                legendgroup=f"Class {target}",
                showlegend=show_legend,
                row=current_row,
                col=current_col,
            )
            fig.update_yaxes(
                tickfont_size=7,
                row=current_row,
                col=current_col,
            )
            fig.update_xaxes(
                title_text=feature,
                titlefont_size=9,
                titlefont_family="Arial Black",
                tickfont_size=7,
                row=current_row,
                col=current_col,
            )

title1 = "Numerical Features - Kernel Density Estimation"
title2 = "Numerical Features - Cumulative Kernel Density Estimation"

for fig, title in zip((fig1, fig2), (title1, title2)):
    fig.update_annotations(font_size=14)
    fig.update_layout(
        font_color=FONT_COLOR,
        title=title,
        title_font_size=18,
        plot_bgcolor=BACKGROUND_COLOR,
        paper_bgcolor=BACKGROUND_COLOR,
        width=840,
        height=1340,
        legend=dict(
            orientation="h",
            yanchor="bottom",
            xanchor="right",
            y=1.01,
            x=1,
        ),
    )

fig1.show()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>You can activate and deactivate distributions for a certain class by clicking on the legend.</li>
    <li>Well, here we've got a diversity of variables, i.e. some of them probably relatively good fit a normal distribution (<code>BN</code>, <code>CU</code>, <code>GH</code>), some have long tails (and extremely long tails), like <code>AR</code>, <code>AY</code>, <code>BR</code>, <code>BZ</code>, etc. Moreover, there are even bimodal distributions (<code>CW</code>, <code>EL</code> and <code>GL</code>).</li>
    <li>We will better understand the diversity between classes on the cumulative plots, as below.</li>
</ul>
</blockquote>

In [14]:
fig2.show()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>The cumulative KDE reveals a varied presence of long tails in the given distributions. Depending on the variable, the responsibility for the long tail can be attributed to values associated with Class $0$ in some cases, while in other cases it is associated with values linked to Class $1$. Additionally, there are instances where the distributions overlap.</li>
</ul>
</blockquote>

# <p style="padding: 15px; background-color: #010D36; font-family: 'JetBrains Mono'; font-weight: bold; font-size: 100%; color: #f2f2f0; letter-spacing: 2px; text-align: center; border-radius: 8px;">Probability Plots &amp; Transformations</p>

<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Notes</b> 📜
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>This section aims to explore so-called probability plots. It's a pleasant graphical technique to assess whether a variable follows a specific distribution. Here, the normal one. On such a plot, samples which follow normal distribution are deployed on a diagonal straight line.</li>
    <li>The mentioned technique helps to decide which transformations should be done within the given variable to improve the fit to the normal distribution.</li>
    <li>Some machine learning models assume that the variable follows a normal distribution. In turn, the mentioned technique helps to decide which transformations should be done within the given variable to improve the fit to that distribution.</li>
    <li>Let's get started with original values and see results.</li>
</ul>
</blockquote>

In [246]:
fig = make_subplots(
    rows=n_rows,
    cols=n_cols,
    y_title="Observed Values",
    x_title="Theoretical Quantiles",
    horizontal_spacing=0.06,
    vertical_spacing=0.04,
)
fig.update_annotations(font_size=14)

for (row, col), feature in zip(axes, numeric_cols):
    (osm, osr), (slope, intercept, R) = probplot(train[feature].dropna(), rvalue=True)
    x_theory = np.array([osm[0], osm[-1]])
    y_theory = intercept + slope * x_theory
    R2 = f"R\u00b2 = {R * R:.2f}"
    fig.add_scatter(x=osm, y=osr, mode="markers", row=row, col=col, name=feature)
    fig.add_scatter(x=x_theory, y=y_theory, mode="lines", row=row, col=col)
    fig.add_annotation(
        x=-1.25,
        y=osr[-1] * 0.75,
        text=R2,
        showarrow=False,
        row=row,
        col=col,
        font_size=9,
    )
    fig.update_yaxes(tickfont_size=7, row=row, col=col)
    fig.update_xaxes(
        title_text=feature,
        titlefont_size=9,
        titlefont_family="Arial Black",
        tickfont_size=7,
        row=row,
        col=col,
    )

fig.update_layout(
    font_color=FONT_COLOR,
    title="Numerical Features - Probability Plots",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    showlegend=False,
    width=840,
    height=1340,
)
fig.update_traces(
    marker=dict(size=1, symbol="x-thin", line=dict(width=2, color="#010D36")),
    line_color="#FF2079",
)
fig.show()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>As you can see, some variables fit a normal distribution well, which manifests by a high coefficient of determination (R-squared) and evenly deployed samples around the straight line. These are for example <code>DN</code> or <code>BN</code>.</li>
    <li>Nevertheless, there are a lot of features which do not fit the normal one. We can improve that by specific transformations:</li>
    <ul style="
        font-size: 16px;
        font-family: 'JetBrains Mono';
        color: #f2f2f0;
        margin-right: 8px;
    ">
        <li><b>Log Transformation</b> - generally works fine with right-skewed data.</li>
        <li><b>Square Root Transformation</b> - similarly to log-level transformation.</li>
        <li><b>Square Transformation</b> - helps to reduce left-skewed data.</li>
        <li><b>Reciprocal Transformation</b> - used sometimes, when data is skewed, or there are obvious outliers.</li>
        <li><b>Box-Cox Transformation</b> - used when data is skewed or has outliers.</li>
        <li><b>Yeo-Johnson Transformation</b> - variation of Box-Cox transformation.</li>
    </ul>
    <li>Let's check all of these transformations for our variables.</li>
</blockquote>

In [297]:
r2_scores = defaultdict(tuple)

for feature in numeric_cols:
    orig = train[feature].dropna()
    _, (*_, R_orig) = probplot(orig, rvalue=True)
    _, (*_, R_log) = probplot(np.log(orig), rvalue=True)
    _, (*_, R_sqrt) = probplot(np.sqrt(orig), rvalue=True)
    _, (*_, R_reci) = probplot(np.reciprocal(orig), rvalue=True)
    _, (*_, R_boxcox) = probplot(stats.boxcox(orig)[0], rvalue=True)
    _, (*_, R_yeojohn) = probplot(stats.yeojohnson(orig)[0], rvalue=True)
    r2_scores[feature] = (
        R_orig * R_orig,
        R_log * R_log,
        R_sqrt * R_sqrt,
        R_reci * R_reci,
        R_boxcox * R_boxcox,
        R_yeojohn * R_yeojohn,
    )

r2_scores = pd.DataFrame(
    r2_scores, index=("Original", "Log", "Sqrt", "Reciprocal", "BoxCox", "YeoJohnson")
).T

r2_scores["Winner"] = r2_scores.idxmax(axis=1)
r2_scores.style.set_table_styles(DF_STYLE).format(precision=3)


In [310]:
r2_scores.describe().T.drop("count", axis=1).rename(
    columns=str.title
).style.set_table_styles(DF_STYLE).format(precision=3)


In [306]:
orig_cols = r2_scores.query("Winner == 'Original'").index.to_list()
log_cols = r2_scores.query("Winner == 'Log'").index.to_list()
sqrt_cols = r2_scores.query("Winner == 'Sqrt'").index.to_list()
reci_cols = r2_scores.query("Winner == 'Reciprocal'").index.to_list()
box_cox_cols = r2_scores.query("Winner == 'BoxCox'").index.to_list()
yeo_johnson_cols = r2_scores.query("Winner == 'YeoJohnson'").index.to_list()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>Well, as you can see Yeo-Johnson's transformation wins in most cases. However, some simple transformations, like log one, are also doing well. Moreover, we have one feature where none of the transformations helps - <code>CW</code>.</li>
</blockquote>

In [292]:
AB_orig = train.AB.dropna()
(osm, osr), (slope, intercept, R) = probplot(AB_orig, rvalue=True)
x_theory = np.array([osm[0], osm[-1]])
y_theory = intercept + slope * x_theory

fig = make_subplots(rows=1, cols=2, subplot_titles=["Probability Plot", "Histogram"])

fig.add_scatter(x=osm, y=osr, mode="markers", row=1, col=1, name="BoxCox(AB)")
fig.add_scatter(x=x_theory, y=y_theory, mode="lines", row=1, col=1)
fig.add_annotation(
    x=-1.25,
    y=osr[-1] * 0.4,
    text=f"R\u00b2 = {R * R:.3f}",
    showarrow=False,
    row=1,
    col=1,
)
fig.update_yaxes(title_text="Observed Values", row=1, col=1)
fig.update_xaxes(title_text="Theoretical Quantiles", row=1, col=1)
fig.update_traces(
    marker=dict(size=1, symbol="x-thin", line=dict(width=2, color="#010D36")),
    line_color="#FF2079",
)

fig.add_histogram(
    x=AB_orig,
    marker_color="#010D36",
    opacity=0.75,
    name="BoxCox(AB)",
    row=1,
    col=2,
)
fig.update_yaxes(title_text="Count", row=1, col=2)
fig.update_xaxes(title_text="BoxCox(AB)", row=1, col=2)

fig.update_layout(
    font_color=FONT_COLOR,
    title="AB Feature - Original",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    showlegend=False,
    width=840,
    height=440,
    bargap=0.2,
)

fig.update_annotations(font_size=14)
fig.show()


In [293]:
AB_transformed = stats.boxcox(train.AB.dropna())[0]
(osm, osr), (slope, intercept, R) = probplot(AB_transformed, rvalue=True)
x_theory = np.array([osm[0], osm[-1]])
y_theory = intercept + slope * x_theory

fig = make_subplots(rows=1, cols=2, subplot_titles=["Probability Plot", "Histogram"])

fig.add_scatter(x=osm, y=osr, mode="markers", row=1, col=1, name="BoxCox(AB)")
fig.add_scatter(x=x_theory, y=y_theory, mode="lines", row=1, col=1)
fig.add_annotation(
    x=-1.25,
    y=osr[-1] * 0.4,
    text=f"R\u00b2 = {R * R:.3f}",
    showarrow=False,
    row=1,
    col=1,
)
fig.update_yaxes(title_text="Observed Values", row=1, col=1)
fig.update_xaxes(title_text="Theoretical Quantiles", row=1, col=1)
fig.update_traces(
    marker=dict(size=1, symbol="x-thin", line=dict(width=2, color="#010D36")),
    line_color="#FF2079",
)

fig.add_histogram(
    x=AB_transformed,
    marker_color="#010D36",
    opacity=0.75,
    name="BoxCox(AB)",
    row=1,
    col=2,
)
fig.update_yaxes(title_text="Count", row=1, col=2)
fig.update_xaxes(title_text="BoxCox(AB)", row=1, col=2)

fig.update_layout(
    font_color=FONT_COLOR,
    title="AB Feature - Box-Cox Transformation",
    title_font_size=18,
    plot_bgcolor=BACKGROUND_COLOR,
    paper_bgcolor=BACKGROUND_COLOR,
    showlegend=False,
    width=840,
    height=440,
    bargap=0.2,
)

fig.update_annotations(font_size=14)
fig.show()


<p style="
    font-size: 20px;
    font-family: 'JetBrains Mono';
    color: #3E3F4C;
    border-bottom: 3px solid #01CBEE;
">
    <b>Observations</b> 📔
</p>

<blockquote style="
    margin-right: auto; 
    margin-left: auto; 
    background-color: #010D36; 
    padding: 15px; 
    border-radius: 8px;
    border-left: none;
">
<ul style="
    font-size: 16px;
    font-family: 'JetBrains Mono';
    color: #f2f2f0;
    margin-left: 8px;
    margin-right: 8px;
    margin-top: 4px; 
    margin-bottom: 4px;
">
    <li>As you can see above, the Box-Cox transformation works perfectly for the <code>AB</code> variable.</li>
    <li>Obviously, I suppose we will be working with tree-based models at the end, but sometimes models like <code>SVC</code> handle very well, and appropriate transformations for these algorithms are crucial.</li>
</blockquote>